
# Theil-Sen 回归

在一个合成数据集上计算 Theil-Sen 回归。

有关回归器的更多信息，请参见 `theil_sen_regression` 。

与 OLS（普通最小二乘）估计量相比，Theil-Sen 估计量对异常值具有鲁棒性。在简单线性回归的情况下，它的崩溃点约为 29.3%，这意味着它可以容忍高达 29.3% 的二维数据中的任意损坏数据（异常值）。

模型的估计是通过计算所有可能的 p 个子样本点组合的斜率和截距来完成的。如果拟合截距，p 必须大于或等于 n_features + 1。最终的斜率和截距定义为这些斜率和截距的空间中位数。

在某些情况下，Theil-Sen 的表现优于同样是鲁棒方法的 `RANSAC <ransac_regression>` 。这在下面的第二个示例中得到了说明，其中相对于 x 轴的异常值扰乱了 RANSAC。调整 RANSAC 的 ``residual_threshold`` 参数可以解决这个问题，但通常需要对数据和异常值的性质有先验知识。
由于 Theil-Sen 的计算复杂性，建议仅在样本数量和特征数量较少的小问题上使用它。对于较大的问题， ``max_subpopulation`` 参数限制了所有可能的 p 个子样本点组合的规模到一个随机选择的子集，因此也限制了运行时间。因此，Theil-Sen 适用于较大的问题，但代价是失去了一些数学特性，因为它在随机子集上工作。


In [ ]:
# 作者：scikit-learn 开发者
# SPDX-License-Identifier：BSD-3-Clause

import time

import matplotlib.pyplot as plt
import numpy as np

from sklearn.linear_model import LinearRegression, RANSACRegressor, TheilSenRegressor

estimators = [
    ("OLS", LinearRegression()),
    ("Theil-Sen", TheilSenRegressor(random_state=42)),
    ("RANSAC", RANSACRegressor(random_state=42)),
]
colors = {"OLS": "turquoise", "Theil-Sen": "gold", "RANSAC": "lightgreen"}
lw = 2

## 仅在 y 方向上的异常值



In [ ]:
np.random.seed(0)
n_samples = 200
# 线性模型 y = 3*x + N(2, 0.1**2)
x = np.random.randn(n_samples)
w = 3.0
c = 2.0
noise = 0.1 * np.random.randn(n_samples)
y = w * x + c + noise
# 10% outliers
y[-20:] += -20 * x[-20:]
X = x[:, np.newaxis]

plt.scatter(x, y, color="indigo", marker="x", s=40)
line_x = np.array([-3, 3])
for name, estimator in estimators:
    t0 = time.time()
    estimator.fit(X, y)
    elapsed_time = time.time() - t0
    y_pred = estimator.predict(line_x.reshape(2, 1))
    plt.plot(
        line_x,
        y_pred,
        color=colors[name],
        linewidth=lw,
        label="%s (fit time: %.2fs)" % (name, elapsed_time),
    )

plt.axis("tight")
plt.legend(loc="upper left")
_ = plt.title("Corrupt y")

## X 方向上的异常值



In [ ]:
np.random.seed(0)
# 线性模型 y = 3*x + N(2, 0.1**2)
x = np.random.randn(n_samples)
noise = 0.1 * np.random.randn(n_samples)
y = 3 * x + 2 + noise
# 10% outliers
x[-20:] = 9.9
y[-20:] += 22
X = x[:, np.newaxis]

plt.figure()
plt.scatter(x, y, color="indigo", marker="x", s=40)

line_x = np.array([-3, 10])
for name, estimator in estimators:
    t0 = time.time()
    estimator.fit(X, y)
    elapsed_time = time.time() - t0
    y_pred = estimator.predict(line_x.reshape(2, 1))
    plt.plot(
        line_x,
        y_pred,
        color=colors[name],
        linewidth=lw,
        label="%s (fit time: %.2fs)" % (name, elapsed_time),
    )

plt.axis("tight")
plt.legend(loc="upper left")
plt.title("Corrupt x")
plt.show()